In [30]:
import torch
from torch.utils.data import DataLoader
import numpy as np
import pandas as pd
from collections import Counter
import string
import collections
import re

# yelp reviews

In [31]:
from argparse import Namespace

args = Namespace(
    frequency_cutoff=25,
    model_state_file='model.pth',
    review_csv='yelp_small.csv',
    save_dir='model_storage/yelp/',
    vectorizer_file="vectorizer.json",
    batch_size=8,
    early_stopping_criteria=5,
    learning_rate=0.001,
    num_epochs=100,
    seed=1337,
    train_proportion=.8,
    val_proportion=.1,
    test_proportion=.1,
    
)

In [32]:
def preprocess_text(text):
    text = text.lower()
    text = re.sub(r"([.,!?])", r" \1 ", text)
    text = re.sub(r"[^a-zA-Z.,!?]+", r" ", text)
    return text
def convert_stars_thumb(stars):
    if stars > 3:
        return "nice"
    else:
        return "bad"

def split_data(review_subset):
    by_rating = collections.defaultdict(list)
    for _, row in review_subset.iterrows():
        by_rating[row.stars].append(row.to_dict())

    final_list = []
    np.random.seed(args.seed)

    for _, item_list in sorted(by_rating.items()):
        np.random.shuffle(item_list)

        n_total = len(item_list)
        n_train = int(args.train_proportion * n_total)
        n_val = int(args.val_proportion * n_total)
        n_test = int(args.test_proportion * n_total)

        for item in item_list[:n_train]:
            item['split'] = 'train'
        for item in item_list[n_train:n_train+n_val]:
            item['split'] = 'val'
        for item in item_list[n_train+n_val:n_train+n_val+n_test]:
            item['split'] = 'test'

        final_list.extend(item_list)

    final_reviews = pd.DataFrame(final_list)
    final_reviews.text = final_reviews.text.apply(preprocess_text)
    final_reviews.stars = final_reviews.stars.apply(convert_stars_thumb)
    return final_reviews

In [33]:
class ReviewVectorizer(object):
    def __init__(self, review_vocab, rating_vocab):
        self.review_vocab = review_vocab
        self.rating_vocab = rating_vocab
        
    def vectorize(self, review):
        one_hot = np.zeros(len(self.review_vocab), dtype=np.float32)
        for token in review.split(" "):
            if token not in string.punctuation:
                one_hot[self.review_vocab.lookup_token(token)] = 1
        return one_hot
    
    @classmethod
    def from_dataframe(cls, review_df, cutoff=25):
        review_vocab = Vocabulary(add_unk=True)
        rating_vocab = Vocabulary(add_unk=False)
        
        for rating in sorted(set(review_df.stars)):
            rating_vocab.add_token(rating)
            
        word_counts = Counter()
        for review in review_df.text:
            for word in review.split(" "):
                if word not in string.punctuation:
                    word_counts[word] += 1
        for word, count in word_counts.items():
            if count > cutoff:
                review_vocab.add_token(word)
                
        return cls(review_vocab, rating_vocab)
    
    @classmethod
    def from_serializable(cls, contents):
        review_vocab = Vocabulary.from_serializable(contents['review_vocab'])
        rating_vocab = Vocabulary.from_serializable(contents['rating_vocab'])
        
        return cls(review_vocab=review_vocab, rating_vocab=rating_vocab)
    
    def to_serializable(self):
        return {'review_vocab': self.review_vocab.to_serializable(), 
                'rating_vocab': self.rating_vocab.to_serializable()}

In [34]:
from torch.utils.data import Dataset

class ReviewDataset(Dataset):
    def __init__(self, review_df, vectorizer):
        """
        Args: 
            review_df (pendas.DataFrame) the dataset
            vectorizer (reviewVectorizer) vectorizer instantiated from dataset
        """
        self.review_df = review_df
        self._vectorizer = vectorizer
        
        self.train_df = self.review_df[self.review_df.split=="train"]
        self.train_size = len(self.train_df)
        
        self.val_df = self.review_df[self.review_df.split=="val"]
        self.validation_size = len(self.val_df)
        
        self.test_df = self.review_df[self.review_df.split=="test"]
        self.test_size = len(self.test_df)
        
        self._lookup_dict = {"train": (self.train_df, self.train_size),
                             "val": (self.val_df, self.validation_size),
                             "test": (self.test_df, self.test_size)}
        
        self.set_split('train')
        
    @classmethod
    def load_dataset_and_make_vectorizer(cls, review_csv):
        review_df = split_data(pd.read_csv(review_csv))
        return cls(review_df, ReviewVectorizer.from_dataframe(review_df))
    
    def get_vectorizer(self):
        return self._vectorizer
    
    def set_split(self, split="train"):
        self._target_split = split
        self._target_df, self._target_size = self._lookup_dict[split]
        
    def __len__(self):
        return self._target_size
    
    def __getitem__(self, index):
        row = self._target_df.iloc[index]
        
        review_vector = self._vectorizer.vectorize(row.text)
        
        rating_index = self._vectorizer.rating_vocab.lookup_token(row.stars)
        
        return {'x_data': review_vector,
                'y_target': rating_index}
    
    def get_num_batches(self, batch_size):
        return len(self) // batch_size
    
    

In [35]:
class Vocabulary(object):
    """Class to process text and extract Vocabulary for mapping"""
    def __init__(self, token_to_idx=None, add_unk=True, unk_token="<UNK>"):
        if token_to_idx is None:
            token_to_idx = {}
        self._token_to_idx = token_to_idx
        self._idx_to_token = {idx: token for token, idx in self._token_to_idx.items()}
        self._add_unk = add_unk
        self._unk_token = unk_token
        self.unk_token = -1
        if add_unk:
            self.unk_index = self.add_token(unk_token)
    
    def to_serializable(self):
        return {'token_to_idx': self.token_to_idx, 'add_unk': self._add_unk,
                'unk_token': self._unk_token}
    
    @classmethod
    def from_serializable(cls, content):
        return cls(**content)
    
    def add_token(self, token):
        if token in self._token_to_idx:
            index = self._token_to_idx[token]
        else:
            index = len(self._token_to_idx)
            self._token_to_idx[token] = index
            self._idx_to_token[index] = token
        return index
    
    def lookup_token(self, token):
        if self._add_unk:
            return self._token_to_idx.get(token, self.unk_index)
        else:
            return self._token_to_idx[token]
        
    def lookup_index(self, index):
        if index not in self._idx_to_token:
            raise KeyError("the index (%d) is not in the Vocabulary" % index)
        return self._idx_to_token[index]
    
    def __str__(self):
        return "<Vocabulary(size=%d)" % len(self)
    
    def __len__(self):
        return len(self._token_to_idx)

In [36]:
def generate_batches(dataset, batch_size, shuffle=True, drop_last=True, device="cpu"):
    dataloader = DataLoader(dataset=dataset, batch_size=batch_size,
                           shuffle=shuffle, drop_last=drop_last, generator=torch.Generator())
    dataloader
    for data_dict in dataloader:
        out_data_dict = {}
        for name, tensor in data_dict.items():
            out_data_dict[name] = data_dict[name].to(device)
        yield out_data_dict

In [37]:
import torch.nn as nn
import torch.nn.functional as F

class ReviewClassifier(nn.Module):
    def __init__(self, num_features):
        super(ReviewClassifier, self).__init__()
        self.fc1 = nn.Linear(in_features=num_features, out_features=1)
        
    def forward(self, x_in, apply_sigmoid=False):
        y_out = self.fc1(x_in).squeeze()
        if apply_sigmoid:
            y_out = F.sigmoid(y_out)
        return y_out

In [38]:
import torch.optim as optim

def make_train_state(args):
    return {'epoch_index': 0, 
           'train_loss': [],
            'train_acc': [],
           'val_loss': [],
            'val_acc': [],
            'test_loss': -1,
            'test_acc': -1}
train_state = make_train_state(args)

args.device = "cpu"

dataset = ReviewDataset.load_dataset_and_make_vectorizer(args.review_csv)
vectorizer = dataset.get_vectorizer()

classifier = ReviewClassifier(num_features=len(vectorizer.review_vocab))
classifier = classifier.to(args.device)

loss_func = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(classifier.parameters(), lr=args.learning_rate)

In [39]:
dataset._vectorizer.rating_vocab._token_to_idx

{'bad': 0, 'nice': 1}

In [40]:
dataset.set_split('train')
batch_generator = generate_batches(dataset, batch_size=args.batch_size,)
for batch_index, batch_dict in enumerate(batch_generator):
    print(batch_dict)
    if batch_index > 3:
        break


{'x_data': tensor([[1., 0., 0.,  ..., 0., 1., 0.],
        [1., 0., 0.,  ..., 0., 0., 0.],
        [1., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [1., 0., 0.,  ..., 0., 0., 0.],
        [1., 0., 0.,  ..., 0., 0., 0.],
        [1., 0., 0.,  ..., 0., 0., 0.]]), 'y_target': tensor([0, 0, 1, 0, 1, 1, 1, 0])}
{'x_data': tensor([[1., 0., 0.,  ..., 0., 0., 0.],
        [1., 0., 0.,  ..., 0., 0., 0.],
        [1., 1., 1.,  ..., 0., 0., 0.],
        ...,
        [1., 1., 0.,  ..., 0., 0., 0.],
        [1., 0., 0.,  ..., 0., 0., 0.],
        [1., 0., 0.,  ..., 0., 0., 0.]]), 'y_target': tensor([0, 1, 1, 0, 0, 0, 0, 1])}
{'x_data': tensor([[1., 0., 0.,  ..., 0., 0., 0.],
        [1., 1., 0.,  ..., 0., 0., 0.],
        [1., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [1., 1., 0.,  ..., 0., 0., 0.],
        [1., 0., 0.,  ..., 0., 0., 0.],
        [1., 0., 0.,  ..., 0., 0., 0.]]), 'y_target': tensor([0, 1, 0, 1, 1, 0, 0, 1])}
{'x_data': tensor([[1., 0., 0.,  ..., 0., 0., 0.],
        [1., 

In [84]:
def compute_accuracy(pred, target):
    probability_value = F.sigmoid(pred).gt(0.5)
    
    true_pos = (probability_value + target) == 2
    true_neg = (probability_value + target) == 0
    true_sum = true_pos.sum() + true_neg.sum()

    return (true_sum/pred.size(dim=0)).item()

In [42]:

for epoch_index in range(args.num_epochs):
    train_state['epoch_index'] = epoch_index
    
    dataset.set_split('train')
    batch_generator = generate_batches(dataset, batch_size=args.batch_size,)
    running_loss=0.0
    running_acc =0.0
    classifier.train()
    
    for batch_index, batch_dict in enumerate(batch_generator):
        optimizer.zero_grad()
        
        y_pred = classifier(x_in=batch_dict['x_data'].float())

        
        loss = loss_func(y_pred, batch_dict['y_target'].float())
        loss_batch = loss.item()
        running_loss += (loss_batch - running_loss) / (batch_index + 1)
        
        loss.backward()
        
        optimizer.step()
        
        acc_batch = compute_accuracy(y_pred, batch_dict['y_target'])
        #running_acc (acc_batch - running_acc) / (batch_index + 1)
    
    #train_state['train_loss'].append(running_loss)
    #train_state['train_acc'].append(running_acc)
    
    dataset.set_split("train") # should be val
    batch_generator = generate_batches(dataset, batch_size=args.batch_size,)
    running_loss=0.0
    running_acc =0.0
    classifier.eval()
    
    for batch_index, batch_dict in enumerate(batch_generator):
        optimizer.zero_grad()
        
        y_pred = classifier(x_in=batch_dict['x_data'].float())
        
        loss = loss_func(y_pred, batch_dict['y_target'].float())
        loss_batch = loss.item()
        running_loss += (loss_batch - running_loss) / (batch_index + 1)
        
        
        #acc_batch = compute_accuracy(y_pred, batch_dict['y_target'])
        #running_acc = (acc_batch - running_acc) / (batch_index + 1)
    #train_state['val_loss'].append(running_loss)
    #train_state['val_acc'].append(running_acc)

test: 
tensor([-0.0248, -0.1589, -0.0864, -0.0242,  0.0127, -0.1502,  0.0315, -0.0657],
       grad_fn=<SqueezeBackward0>)
tensor([0, 0, 1, 0, 1, 1, 1, 0])
tensor([0.4938, 0.4604, 0.4784, 0.4939, 0.5032, 0.4625, 0.5079, 0.4836],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([-0.1823,  0.0239, -0.0535, -0.0491, -0.0111, -0.1628, -0.1861, -0.1315],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 1, 0, 0, 0, 0, 1])
tensor([0.4545, 0.5060, 0.4866, 0.4877, 0.4972, 0.4594, 0.4536, 0.4672],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ 0.0354, -0.3589, -0.0199,  0.1281, -0.0614, -0.0771,  0.0059, -0.0552],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 0, 1, 1, 0, 0, 1])
tensor([0.5088, 0.4112, 0.4950, 0.5320, 0.4846, 0.4807, 0.5015, 0.4862],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([-0.0726, -0.2873, -0.2141, -0.0096, -0.0705, -0.3523, -0.0336, -0.2199],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 1, 0, 1, 1, 0, 1])
tensor([0.4818, 0.4287, 0.4467, 0.4976, 0.4824, 0.41

test: 
tensor([0.4793, 0.2682, 0.2027, 0.3817, 0.5754, 0.6680, 0.4732, 0.2206],
       grad_fn=<SqueezeBackward0>)
tensor([1, 0, 0, 1, 1, 1, 0, 0])
tensor([0.6176, 0.5666, 0.5505, 0.5943, 0.6400, 0.6611, 0.6161, 0.5549],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([-0.0428,  0.2153,  0.2379,  0.4639,  0.1300,  0.3293,  0.4190,  0.1137],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 0, 1, 1, 1, 0])
tensor([0.4893, 0.5536, 0.5592, 0.6139, 0.5325, 0.5816, 0.6033, 0.5284],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([0.7293, 0.2302, 0.7242, 0.3018, 0.2301, 0.4980, 0.3990, 0.4414],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 1, 1, 1, 1, 0])
tensor([0.6746, 0.5573, 0.6735, 0.5749, 0.5573, 0.6220, 0.5985, 0.6086],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([0.5513, 0.2021, 0.1017, 0.0133, 0.2059, 0.1527, 0.3700, 0.2631],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 0, 0, 0, 1, 0])
tensor([0.6344, 0.5504, 0.5254, 0.5033, 0.5513, 0.5381, 0.5915, 0.5654],
   

/gnu/store/1bvl1h35c5ylr2ps8nnx60h5l47smrqw-profile/lib/python3.9/site-packages/torch/nn/functional.py:1960: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


test: 
tensor([0.2662, 0.1071, 0.1369, 0.8422, 0.2658, 0.4816, 0.4033, 0.1651],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 1, 1, 0, 0, 1, 0])
tensor([0.5662, 0.5267, 0.5342, 0.6989, 0.5661, 0.6181, 0.5995, 0.5412],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ 0.1850,  0.2596,  0.2695,  0.0501,  0.0815, -0.1742,  0.3471,  0.0986],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 1, 1, 0, 0, 1])
tensor([0.5461, 0.5645, 0.5670, 0.5125, 0.5204, 0.4566, 0.5859, 0.5246],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ 0.1538,  0.3341, -0.0487,  0.3324, -0.0804,  0.4017,  0.1185,  0.1994],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 1, 1, 0, 1, 1, 0])
tensor([0.5384, 0.5828, 0.4878, 0.5823, 0.4799, 0.5991, 0.5296, 0.5497],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ 0.1166,  0.2995,  0.3595,  0.0078,  0.0938, -0.0366,  0.1887,  0.1310],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 0, 0, 0, 1, 0])
tensor([0.5291, 0.5743, 0.5889, 0.5020, 0.5234, 0.4909, 0.54

test: 
tensor([ 0.2685,  0.3960,  0.4077,  0.0624,  0.0653, -0.0917, -0.0147,  0.2710],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 0, 0, 0, 0, 1])
tensor([0.5667, 0.5977, 0.6005, 0.5156, 0.5163, 0.4771, 0.4963, 0.5673],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ 0.3961,  0.1874, -0.2074,  0.2970,  0.0107,  0.1795,  0.3932,  0.4249],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 0, 0, 1, 1, 1])
tensor([0.5978, 0.5467, 0.4483, 0.5737, 0.5027, 0.5448, 0.5970, 0.6047],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ 0.1592, -0.2115,  0.0962,  0.2180,  0.2296,  0.4190,  0.3345,  0.3544],
       grad_fn=<SqueezeBackward0>)
tensor([0, 0, 1, 0, 0, 1, 0, 1])
tensor([0.5397, 0.4473, 0.5240, 0.5543, 0.5571, 0.6032, 0.5829, 0.5877],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ 0.0645,  0.5006,  0.2112,  0.1719,  0.1477, -0.0868, -0.1689,  0.0416],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 1, 1, 1, 0, 0, 0])
tensor([0.5161, 0.6226, 0.5526, 0.5429, 0.5369, 0.47

...

test: 
tensor([ 3.3423,  3.5495,  5.1182, -3.8551, -2.0265, -8.4141,  1.9986, -1.1538],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 0, 0, 0, 1, 0])
tensor([9.6585e-01, 9.7206e-01, 9.9405e-01, 2.0732e-02, 1.1645e-01, 2.2167e-04,
        8.8065e-01, 2.3980e-01], grad_fn=<SigmoidBackward0>)
test: 
tensor([-7.9575,  3.6017,  2.0278,  8.4602, -3.6143,  4.7548, -3.3395,  1.6031],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 1, 1, 0, 1, 0, 1])
tensor([3.4991e-04, 9.7345e-01, 8.8369e-01, 9.9979e-01, 2.6230e-02, 9.9146e-01,
        3.4241e-02, 8.3245e-01], grad_fn=<SigmoidBackward0>)
test: 
tensor([-5.2392,  9.5316, -3.7670,  6.4838, -2.4811,  7.7768,  2.2295,  2.0488],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 0, 1, 0, 1, 1, 1])
tensor([0.0053, 0.9999, 0.0226, 0.9985, 0.0772, 0.9996, 0.9029, 0.8858],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ -2.2403, -11.7484,   7.6076,  -3.0040,  -5.8635,   3.1919,  -3.4585,
         -2.0395], grad_fn=<SqueezeBackward0>)
tensor([0,

tensor([ 3.9095,  1.6438,  2.0956,  4.0386, -6.0997,  1.5641, -2.6646,  3.6268],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 1, 0, 1, 0, 1])
tensor([0.9803, 0.8381, 0.8905, 0.9827, 0.0022, 0.8269, 0.0651, 0.9741],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([  4.0285,  -3.4033,   5.5823,   3.3660, -11.9173,   6.3004,  -9.3042,
         -5.0345], grad_fn=<SqueezeBackward0>)
tensor([1, 0, 1, 1, 0, 1, 0, 0])
tensor([9.8251e-01, 3.2192e-02, 9.9625e-01, 9.6662e-01, 6.6736e-06, 9.9817e-01,
        9.1037e-05, 6.4673e-03], grad_fn=<SigmoidBackward0>)
test: 
tensor([ 1.2475, -4.0296,  4.7921,  1.4898,  1.8611, -3.3945, -1.4648, -1.9344],
       grad_fn=<SqueezeBackward0>)
tensor([1, 0, 1, 1, 1, 0, 0, 0])
tensor([0.7769, 0.0175, 0.9918, 0.8160, 0.8654, 0.0325, 0.1877, 0.1263],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ 3.2605,  1.4838,  2.5075, -2.6907,  2.4262, -9.8080, -3.0644,  3.9519],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 0, 1, 0, 0, 1])
tensor([9.6305e-0

test: 
tensor([-1.6644, -1.8973,  2.2339, -4.0178,  2.6006,  4.9043,  5.2441, -4.2832],
       grad_fn=<SqueezeBackward0>)
tensor([0, 0, 1, 0, 1, 1, 1, 0])
tensor([0.1592, 0.1304, 0.9033, 0.0177, 0.9309, 0.9926, 0.9947, 0.0136],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ -4.2171,   4.1141,   2.8637,  -3.7032,  -6.0269,  -2.4134, -11.5036,
          3.9226], grad_fn=<SqueezeBackward0>)
tensor([0, 1, 1, 0, 0, 0, 0, 1])
tensor([1.4527e-02, 9.8392e-01, 9.4602e-01, 2.4051e-02, 2.4071e-03, 8.2154e-02,
        1.0093e-05, 9.8060e-01], grad_fn=<SigmoidBackward0>)
test: 
tensor([ -2.4863,  11.7226,  -2.4294,   6.3926,   2.1719,  -2.2782, -13.6311,
          5.1449], grad_fn=<SqueezeBackward0>)
tensor([0, 1, 0, 1, 1, 0, 0, 1])
tensor([7.6825e-02, 9.9999e-01, 8.0956e-02, 9.9833e-01, 8.9770e-01, 9.2947e-02,
        1.2025e-06, 9.9420e-01], grad_fn=<SigmoidBackward0>)
test: 
tensor([ -8.4306,   3.3127,   3.9450,  -3.4723,   5.9361,   5.1671, -10.1755,
          2.6565], grad_fn=<SqueezeBack

test: 
tensor([-2.3101,  1.6861,  1.6218,  5.4945, -2.9819, 12.8437,  4.2028, -4.9471],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 1, 1, 0, 1, 1, 0])
tensor([0.0903, 0.8437, 0.8350, 0.9959, 0.0483, 1.0000, 0.9853, 0.0071],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ 3.3553,  3.5706,  5.1373, -3.8757, -2.0416, -8.4782,  2.0113, -1.1670],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 0, 0, 0, 1, 0])
tensor([9.6628e-01, 9.7263e-01, 9.9416e-01, 2.0319e-02, 1.1491e-01, 2.0791e-04,
        8.8198e-01, 2.3739e-01], grad_fn=<SigmoidBackward0>)
test: 
tensor([-8.0035,  3.6184,  2.0451,  8.5293, -3.6332,  4.7714, -3.3500,  1.6198],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 1, 1, 0, 1, 0, 1])
tensor([3.3419e-04, 9.7388e-01, 8.8545e-01, 9.9980e-01, 2.5751e-02, 9.9160e-01,
        3.3897e-02, 8.3477e-01], grad_fn=<SigmoidBackward0>)
test: 
tensor([-5.2798,  9.6133, -3.7980,  6.5334, -2.5034,  7.8428,  2.2492,  2.0646],
       grad_fn=<SqueezeBackward0>)
tensor([0, 1, 0, 1,

test: 
tensor([ 2.2450, -2.6436, -2.5176,  3.6418,  2.1356, -2.3806,  0.9133, -4.8477],
       grad_fn=<SqueezeBackward0>)
tensor([1, 0, 0, 1, 1, 0, 1, 0])
tensor([0.9042, 0.0664, 0.0746, 0.9745, 0.8943, 0.0847, 0.7137, 0.0078],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([ 4.4594, -8.7850,  3.6638,  3.7786,  2.4006, -2.1446,  7.2870, -5.8118],
       grad_fn=<SqueezeBackward0>)
tensor([1, 0, 1, 1, 1, 0, 1, 0])
tensor([9.8856e-01, 1.5299e-04, 9.7501e-01, 9.7766e-01, 9.1687e-01, 1.0483e-01,
        9.9932e-01, 2.9830e-03], grad_fn=<SigmoidBackward0>)
test: 
tensor([ 3.9426,  1.6586,  2.1137,  4.0605, -6.1254,  1.5777, -2.6774,  3.6491],
       grad_fn=<SqueezeBackward0>)
tensor([1, 1, 1, 1, 0, 1, 0, 1])
tensor([0.9810, 0.8400, 0.8922, 0.9831, 0.0022, 0.8289, 0.0643, 0.9746],
       grad_fn=<SigmoidBackward0>)
test: 
tensor([  4.0486,  -3.4215,   5.6170,   3.3818, -12.0119,   6.3361,  -9.3778,
         -5.0612], grad_fn=<SqueezeBackward0>)
tensor([1, 0, 1, 1, 0, 1, 0, 0])
tensor([9.

In [43]:
def predict_rating(review, classifier, vectorizer, decision_threshold=0.5):
    """
    review: text to review
    classifier: trained model,
    
    """
    review = preprocess_text(review)
    vectorized_review = torch.tensor(vectorizer.vectorize(review))
    result =classifier (vectorized_review.view(1, -1))
    
    probability_value = F.sigmoid(result).item()

    index = 1
    if probability_value < decision_threshold:
        index = 0
    
    return vectorizer.rating_vocab.lookup_index(index)


In [93]:
dataset.set_split('test')
batch_generator = generate_batches(dataset, batch_size=args.batch_size,)
running_loss=0.0
running_acc = []
classifier.eval()

for batch_index, batch_dict in enumerate(batch_generator):

    y_pred = classifier(x_in=batch_dict['x_data'].float())


    loss = loss_func(y_pred, batch_dict['y_target'].float())
    loss_batch = loss.item()

    running_loss += (loss_batch - running_loss) / (batch_index + 1)


    acc_batch = compute_accuracy(y_pred, batch_dict['y_target'])
    running_acc.append(acc_batch)

train_state['train_loss'].append(running_loss)
train_state['train_acc'].append(running_acc)

print(np.average(running_acc))

0.675


In [45]:
test_review = "this is so bad, I hate it, gross, disagreable"
prediction = predict_rating(test_review, classifier, vectorizer)
print("{} -> {}".format(test_review, prediction))

this is so bad, I hate it, gross, disagreable -> bad


In [46]:
test_review = "this is so good, I like the ambiance and the nice tables"
prediction = predict_rating(test_review, classifier, vectorizer)
print("{} -> {}".format(test_review, prediction))

this is so good, I like the ambiance and the nice tables -> nice


In [47]:
test_review = "smelled like farts"
prediction = predict_rating(test_review, classifier, vectorizer)
print("{} -> {}".format(test_review, prediction))

smelled like farts -> nice


In [48]:
fc1_weights = classifier.fc1.weight.detach()[0]
_, indices = torch.sort(fc1_weights, dim=0, descending=True)
indices = indices.numpy().tolist()

print(" most best:")
for i in range(20):
    print(vectorizer.review_vocab.lookup_index(indices[i]))

 most best:
taken
wonderful
venue
mac
door
dance
enjoyed
yet
perfect
bed
through
free
gets
absolutely
pricey
comfortable
toronto
ladies
truly
ou


In [49]:
print("bad")
indices.reverse()
for i in range(20):
    print(vectorizer.review_vocab.lookup_index(indices[i]))

bad
ok
sad
slow
worst
bill
wasn
shrimp
double
rude
late
elsewhere
spot
under
customers
option
terrible
wouldn
limited
pink
big
